In [1]:
!pwd

/Users/ashish1610dhiman/data_projects/bestbuy/notebooks/ashish


In [2]:
import sys
import matplotlib
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import datetime

sys.version

'3.9.15 | packaged by conda-forge | (main, Nov 22 2022, 08:55:37) \n[Clang 14.0.6 ]'

In [44]:
%load_ext autoreload 
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


### Read data

In [4]:
train_test = pd.read_csv("../../data/train_validation_marker.csv")
train_test["SALES_DATE"] = pd.to_datetime(train_test["SALES_DATE"])
print (train_test.shape)

(846632, 15)


#### Find SKUs with very low volume

In [5]:
#clean train/test
train = train_test[(train_test.validation==False) & (train_test.validation_clean==True)]
validation = train_test[(train_test.validation==True) & (train_test.validation_clean==True)]
train.shape,validation.shape

((797490, 15), (3815, 15))

In [6]:
train[train.SALES_DATE>="2022-03-01"]

Encoded_SKU_ID SALES_DATE        SUBCLASS_NAME           CLASS_NAME  \
8                    8 2022-03-04      ACTION CAM ACCY  DIGITAL CAMERA ACCY   
10                  10 2022-05-22         DECK HARNESS   MOBILE ACCESSORIES   
15                  15 2022-05-26            MISC ACCY   MOBILE ACCESSORIES   
21                  22 2022-07-18   SO GAS COOKTOP REG     BUILT IN COOKING   
26                  28 2022-07-19   SO GAS COOKTOP REG     BUILT IN COOKING   
...                ...        ...                  ...                  ...   
846604              89 2022-04-26   SO TL GAS DRY BBHD              LAUNDRY   
846610             278 2022-03-12  TOP LOAD ELEC DRYER              LAUNDRY   
846611             270 2022-06-04    MISC CAMERA ACCES  DIGITAL CAMERA ACCY   
846612             506 2022-03-04    MISC CAMERA ACCES  DIGITAL CAMERA ACCY   
846617             486 2022-07-23   SO CAR ACCESSORIES   MOBILE ACCESSORIES   

                    ML_NAME          CATEGORY_NAME  RETAIL_PRICE PROMO_PRICE  \
8       ML - DI Accessories   VP - Digital Imaging         19.99           ?   
10       ML - Connected Car   VP - Electrify & Car         79.99           ?   
15       ML - Connected Car   VP - Electrify & Car         19.99           ?   
21             ML - Kitchen  VP - Major Appliances        999.99      699.99   
26             ML - Kitchen  VP - Major Appliances       1298.99           ?   
...                     ...                    ...           ...         ...   
846604         ML - Laundry  VP - Major Appliances        944.99      849.99   
846610         ML - Laundry  VP - Major Appliances        899.99           ?   
846611  ML - DI Accessories   VP - Digital Imaging         44.99           ?   
846612  ML - DI Accessories   VP - Digital Imaging         82.99           ?   
846617   ML - Connected Car   VP - Electrify & Car         16.99           ?   

       COMPETITOR_PRICE      Inventory  DAILY_UNITS max_SALES_DATE  \
8                 13.32  Fully-Stocked            5     2022-07-31   
10                    ?  Fully-Stocked            2     2022-07-31   
15                    ?  Fully-Stocked            0     2022-07-31   
21                  698       Moderate            4     2022-07-31   
26                 1299    Constrained            2     2022-07-31   
...                 ...            ...          ...            ...   
846604              696       Moderate            3     2022-07-31   
846610              999  Fully-Stocked            2     2022-07-31   
846611                ?  Fully-Stocked            3     2022-07-31   
846612               61  Fully-Stocked            1     2022-07-31   
846617                ?  Fully-Stocked            2     2022-07-31   

        delta_days  validation  validation_clean  
8              149       False              True  
10              70       False              True  
15              66       False              True  
21              13       False              True  
26              12       False              True  
...            ...         ...               ...  
846604          96       False              True  
846610         141       False              True  
846611          57       False              True  
846612         149       False              True  
846617           8       False              True  

[74521 rows x 15 columns]

In [7]:
sku_vals = train[train.SALES_DATE>="2022-03-01"].groupby("Encoded_SKU_ID")["DAILY_UNITS"].nunique()

In [8]:
(sku_vals<=6).sum()

163

In [9]:
sku_vals.count()

545

In [10]:
sku_vals

Encoded_SKU_ID
1       7
2      11
3       7
5      11
6      22
       ..
571    13
572     7
573     5
574     5
575     6
Name: DAILY_UNITS, Length: 545, dtype: int64

### Fit HMM on these

In [11]:
sku_in_scope = sku_vals[(sku_vals<=6)]

In [12]:
import sys
sys.path.append("../../")

from src.ad_hmm import sku_predict

In [13]:
pd.options.mode.chained_assignment = None

In [14]:
from tqdm.notebook import tqdm

In [15]:
sku_in_scope.index[:1]

Int64Index([7], dtype='int64', name='Encoded_SKU_ID')

In [16]:
all_preds = []
for sku_id in tqdm(sku_in_scope.index):
    n_comps = sku_in_scope[sku_id]
    sku_pred_model = sku_predict(train_test,sku_id)
    feats_sku = sku_pred_model.get_features(n_lags=2)
    train1,valid1 = sku_pred_model.split_train_test("2022-07-25")
    sku_pred_model.fit_hmm(train1,"2022-03-01", n_components1 = n_comps)
    try:
        sku_pred_15 = sku_pred_model.predict(valid1, 15)
        sku_pred_30 = sku_pred_model.predict(valid1, 30)
        sku_pred_45 = sku_pred_model.predict(valid1, 45)
        sku_pred_60 = sku_pred_model.predict(valid1, 60)
        sku_pred_90 = sku_pred_model.predict(valid1, 90)
        sku_pred_max = sku_pred_model.predict(valid1, sku_pred_model.X.shape[0])
        merge0 = sku_pred_15[["predicted"]].merge(sku_pred_30[["predicted"]],left_index = True,\
                              right_index = True, suffixes=("","_30"))
        merge1 = merge0.merge(sku_pred_45[["predicted"]],left_index = True,\
                              right_index = True, suffixes=("","_45"))
        merge2 = merge1.merge(sku_pred_60[["predicted"]],left_index = True,\
                              right_index = True, suffixes=("","_60"))
        merge3 = merge2.merge(sku_pred_90[["predicted"]],left_index = True,\
                              right_index = True, suffixes=("","_90"))
        merge4 = merge2.merge(sku_pred_max[["predicted"]],left_index = True,\
                              right_index = True, suffixes=("","_max"))
        merge4["Encoded_SKU_ID"] =[sku_id]*merge4.shape[0]
        all_preds.append(merge4)
    except:
        print (f"Error for {sku_id}")

  0%|          | 0/163 [00:00<?, ?it/s]

Created 2 lag features
Training on : ['DAILY_UNITS_lag1', 'DAILY_UNITS_lag2'] ['change_lag1', 'change_lag2']


/Users/ashish1610dhiman/opt/anaconda3/envs/bestbuy/lib/python3.9/site-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


Starting Prediction
-----> Predicting for day:0


Even though the 'startprob_' attribute is set, it will be overwritten during initialization because 'init_params' contains 's'
Even though the 'transmat_' attribute is set, it will be overwritten during initialization because 'init_params' contains 't'
Fitting a model with 83 free scalar parameters with only 60 data points will result in a degenerate solution.
Even though the 'means_' attribute is set, it will be overwritten during initialization because 'init_params' contains 'm'
/Users/ashish1610dhiman/opt/anaconda3/envs/bestbuy/lib/python3.9/site-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
Even though the 'covars_' attribute is set, it will be overwritten during initialization because 'init_params' contains 'c'


...

-----> Predicting for day:4


Even though the 'startprob_' attribute is set, it will be overwritten during initialization because 'init_params' contains 's'
Even though the 'transmat_' attribute is set, it will be overwritten during initialization because 'init_params' contains 't'
Even though the 'means_' attribute is set, it will be overwritten during initialization because 'init_params' contains 'm'
/Users/ashish1610dhiman/opt/anaconda3/envs/bestbuy/lib/python3.9/site-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
Even though the 'covars_' attribute is set, it will be overwritten during initialization because 'init_params' contains 'c'


-----> Predicting for day:5


Even though the 'startprob_' attribute is set, it will be overwritten during initialization because 'init_params' contains 's'
Even though the 'transmat_' attribute is set, it will be overwritten during initialization because 'init_params' contains 't'
Even though the 'means_' attribute is set, it will be overwritten during initialization because 'init_params' contains 'm'
/Users/ashish1610dhiman/opt/anaconda3/envs/bestbuy/lib/python3.9/site-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
Even though the 'covars_' attribute is set, it will be overwritten during initialization because 'init_params' contains 'c'


-----> Predicting for day:6


### Analyse result

In [19]:
hmm_result = pd.concat(all_preds)
hmm_result.head()

predicted  predicted_30  predicted_45  predicted_60  \
2022-07-25        1.0           0.0           0.5           1.0   
2022-07-26        1.0           0.5           1.0           1.5   
2022-07-27        1.0           0.5           0.5           1.5   
2022-07-28        0.0           0.5           2.0           1.5   
2022-07-29        2.0           0.5           0.0           0.5   

            predicted_max  Encoded_SKU_ID  
2022-07-25            1.0               7  
2022-07-26            0.5               7  
2022-07-27            0.5               7  
2022-07-28            1.0               7  
2022-07-29            1.0               7

In [20]:
hmm_result.to_csv("../../data/hmm_result_v0.csv")

### RMSE

In [21]:
validation

Encoded_SKU_ID SALES_DATE      SUBCLASS_NAME           CLASS_NAME  \
100                 96 2022-07-27  SO RANGEHOODS REG  KITCHEN VENTILATION   
218                187 2022-07-29          MISC ACCY   MOBILE ACCESSORIES   
420                297 2022-07-29        POWERSPORTS           CAR STEREO   
652                372 2022-07-27          DASH KITS   MOBILE ACCESSORIES   
831                412 2022-07-26   TOP MOUNT REFRIG        REFRIGERATION   
...                ...        ...                ...                  ...   
844807             159 2022-07-27      SO REFRIG REG        REFRIGERATION   
844981              25 2022-07-29            TRIPODS  DIGITAL CAMERA ACCY   
845659             495 2022-07-26           SO PARTS   MOBILE ACCESSORIES   
845855              68 2022-07-29          DASH KITS   MOBILE ACCESSORIES   
845859             411 2022-07-30   CAMERA BATTERIES  DIGITAL CAMERA ACCY   

                    ML_NAME          CATEGORY_NAME  RETAIL_PRICE PROMO_PRICE  \
100            ML - Kitchen  VP - Major Appliances        355.99           ?   
218      ML - Connected Car   VP - Electrify & Car         13.99           ?   
420      ML - Connected Car   VP - Electrify & Car        169.99           ?   
652      ML - Connected Car   VP - Electrify & Car         16.99           ?   
831            ML - Kitchen  VP - Major Appliances        989.99           ?   
...                     ...                    ...           ...         ...   
844807         ML - Kitchen  VP - Major Appliances       3419.99           ?   
844981  ML - DI Accessories   VP - Digital Imaging        149.99           ?   
845659   ML - Connected Car   VP - Electrify & Car         49.99           ?   
845855   ML - Connected Car   VP - Electrify & Car         16.99           ?   
845859  ML - DI Accessories   VP - Digital Imaging         39.99           ?   

       COMPETITOR_PRICE      Inventory  DAILY_UNITS max_SALES_DATE  \
100                   ?    Constrained            2     2022-07-31   
218                   ?  Fully-Stocked            0     2022-07-31   
420                   ?  Fully-Stocked            6     2022-07-31   
652                   ?  Fully-Stocked            1     2022-07-31   
831                 988    Constrained            4     2022-07-31   
...                 ...            ...          ...            ...   
844807                ?  Fully-Stocked            1     2022-07-31   
844981                ?  Fully-Stocked            2     2022-07-31   
845659                ?   Out-of-Stock            0     2022-07-31   
845855                ?  Fully-Stocked            2     2022-07-31   
845859                ?  Fully-Stocked            0     2022-07-31   

        delta_days  validation  validation_clean  
100              4        True              True  
218              2        True              True  
420              2        True              True  
652              4        True              True  
831              5        True              True  
...            ...         ...               ...  
844807           4        True              True  
844981           2        True              True  
845659           5        True              True  
845855           2        True              True  
845859           1        True              True  

[3815 rows x 15 columns]

In [22]:
y_act = validation[["Encoded_SKU_ID","SALES_DATE","DAILY_UNITS"]].rename(columns = {"DAILY_UNITS":"actual"})
y_act.head()

Encoded_SKU_ID SALES_DATE  actual
100              96 2022-07-27       2
218             187 2022-07-29       0
420             297 2022-07-29       6
652             372 2022-07-27       1
831             412 2022-07-26       4

In [70]:
y_act["actual"]= y_act["actual"].astype("float")

In [46]:
from src.utils import *

In [74]:
y_act.shape

(3815, 3)

In [72]:
y_pred_hmm.dtypes, y_act.dtypes

(Encoded_SKU_ID             int64
 SALES_DATE        datetime64[ns]
 predicted                float64
 dtype: object,
 Encoded_SKU_ID             int64
 SALES_DATE        datetime64[ns]
 actual                   float64
 dtype: object)

In [75]:
for col in hmm_result.columns:
    if "pred" in col:
        y_pred_hmm = hmm_result.reset_index(names = "SALES_DATE")[["Encoded_SKU_ID","SALES_DATE",col\
                                                                  ]].rename(columns={col:"predicted"})
        print (f"For {col}, rmse(hmm) = {rmse(y_act,y_pred_hmm):.4f}")

AssertionError: y_act and y_pred shapes do not match

### Random

sku_id = 7

n_comps = sku_in_scope[sku_id]
sku_pred_model = sku_predict(train_test,sku_id)
feats_sku = sku_pred_model.get_features(n_lags=2)
train1,valid1 = sku_pred_model.split_train_test("2022-07-25")

n_comps

sku_pred_model.fit_hmm(train1,"2022-03-01", n_components1 = n_comps)

sku_pred_model.predict(valid1, 60)

valid1

sku_pred_model._get_most_probable_outcome(sku_pred_model.X[-90:], 100, 100)